In [1]:
import networkx as nx
import pandas as pd
import numpy as np
import random
import openpyxl
import math
import statistics as stats
import shlex
import time
import os

In [2]:
def list_contains(List1, List2): 
    check = []
  
    # add elements in list 1 that are in list2
    for m in List1: 
        if (m in List2) & (not (m in check)): 
            check.append(m)
            
    return check

In [3]:
wb_obj = openpyxl.load_workbook('hPPIN_network.xlsx') 
sheet = wb_obj.active

hPPIN = nx.Graph()
for row in sheet.iter_rows(2, sheet.max_row):
    node1 = row[0].value
    node2 = row[1].value
    hPPIN.add_edge(node1, node2, weight=1)
len(list(hPPIN.nodes))

17061

In [5]:
nodes_list = list(hPPIN.nodes)
    
textfile = open("hPPIN_node_list.txt", "w")

for element in nodes_list:

    textfile.write(element + "\n")

textfile.close()

In [5]:
def get_matched_controls(G, genes):
    # only genes in the PPI
    file_genes = pd.read_csv(genes, header = None, names = ['genes'])
    node_list = list(G.nodes)
    gene_list = list_contains(file_genes['genes'], node_list)
    
    # get degrees and repeatsfor each
    gene_list_degrees = [val for (node, val) in hPPIN.degree(gene_list)]
    degree_repeats = dict((i, gene_list_degrees.count(i)) for i in gene_list_degrees)

    # extract  5 fold nodes with the same degree
    matched_controls = []
    for (degree, repeat) in degree_repeats.items():
        controls = [node for (node, val) in hPPIN.degree() if val == degree]
        controls = [x for x in controls if x not in gene_list]
        if len(controls) > (5*repeat):
            matched_controls.extend(random.sample(controls, 5*repeat))
        else:
            matched_controls.extend(controls)
    
    print("Total Genes: " + str(len(file_genes)))
    print("Total Genes in PPI: " + str(len(gene_list)))
    print("Expected Matched Controls: " + str(5*len(gene_list)))
    print("Actual Matched Controls: " + str(len(matched_controls)))
    print("")
    print("Mean degree in set: " + str(stats.mean(gene_list_degrees)))
    print("Mean degree in PPI network: " + str(stats.mean([val for (node, val) in hPPIN.degree()])))
    print("")
            
    return(matched_controls)

In [6]:
def run_sp_matched_controls(genes, filename):
    # split list into groups of 10
    sub_lists = [genes[i:i + 10] for i in range(0, len(genes), 10)]

    # write out matched control list
    for i in range(len(sub_lists)):
        file_in = "./matched_control_paths/" + filename + str(i) + ".txt"
        file_out = "./matched_control_paths/" + filename + str(i) + ".out"
        textfile = open(file_in, 'w') 
        for element in sub_lists[i]:

            textfile.write(element + "\n")

        textfile.close()
        command = "printf \"#!/bin/bash\nmodule load python\npython /data/timonaj/cancer_as_wound/ppi_analysis/cosmic_shortest_paths.py " + file_in + ' ' + file_out + "\" > " + "jobscript" + str(i) + ".job \nsbatch --mem=10g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 " + "jobscript" + str(i) + ".job \n"
        print(command)
        os.system(command)
        
        if i % 80 == 0 and i != 0:
            time.sleep(1200)

In [6]:
regen_matched = get_matched_controls(hPPIN, "regen_genes.txt")
regen_100_matched = get_matched_controls(hPPIN, "regen_genes_100.txt")

Total Genes: 500
Total Genes in PPI: 455
Expected Matched Controls: 2275
Actual Matched Controls: 2209

Mean degree in set: 33.95164835164835
Mean degree in PPI network: 22.096594572416624

Total Genes: 100
Total Genes in PPI: 94
Expected Matched Controls: 470
Actual Matched Controls: 465

Mean degree in set: 30.170212765957448
Mean degree in PPI network: 22.096594572416624



In [7]:
#run_sp_matched_controls(regen_100_matched, "regen_100_matched_controls_")

In [8]:
wound_matched = get_matched_controls(hPPIN, "wound_genes.txt")
wound_100_matched = get_matched_controls(hPPIN, "wound_genes_100.txt")

Total Genes: 500
Total Genes in PPI: 465
Expected Matched Controls: 2325
Actual Matched Controls: 2227

Mean degree in set: 42.468817204301075
Mean degree in PPI network: 22.096594572416624

Total Genes: 100
Total Genes in PPI: 96
Expected Matched Controls: 480
Actual Matched Controls: 462

Mean degree in set: 41.270833333333336
Mean degree in PPI network: 22.096594572416624



In [9]:
#run_sp_matched_controls(wound_100_matched, "wound_100_matched_controls_")

In [10]:
stress_matched = get_matched_controls(hPPIN, "stress_genes.txt")
stress_100_matched = get_matched_controls(hPPIN, "stress_genes_100.txt")

Total Genes: 500
Total Genes in PPI: 362
Expected Matched Controls: 1810
Actual Matched Controls: 1731

Mean degree in set: 34.73756906077348
Mean degree in PPI network: 22.096594572416624

Total Genes: 100
Total Genes in PPI: 71
Expected Matched Controls: 355
Actual Matched Controls: 334

Mean degree in set: 38.436619718309856
Mean degree in PPI network: 22.096594572416624



In [11]:
#run_sp_matched_controls(stress_100_matched, "stress_100_matched_controls_")

In [6]:
def genome_wrs_distance(genes, filename, filename_2,output):
    # split list into groups of 10
    sub_lists = [genes[i:i + 10] for i in range(0, len(genes), 10)]
    
    # write out matched control list
    for i in range(len(sub_lists)):
        file_in1 = "./genome_analysis/" + filename + str(i) + ".txt"
        file_in2 = "/data/timonaj/cancer_as_wound/ppi_analysis/" + filename_2 
        file_out = "./genome_analysis/" + output + str(i) + ".out"
        textfile = open(file_in1, 'w') 
        
        for element in sub_lists[i]:
            textfile.write(element + "\n")
        textfile.close()
            
        command = "printf \"#!/bin/bash\nmodule load python\npython /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py " + file_in1 + ' ' + file_in2 + ' ' + file_out + "\" > " + "./genome_analysis/jobscript" + str(i) + ".job \nsbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 " + "./genome_analysis/jobscript" + str(i) + ".job \n"
        print(command)
        os.system(command)
        
        if i % 500 == 0 and i != 0:
            time.sleep(1200)

In [7]:
#regen
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "regen_genes.txt", "genome_wrs_paths")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

31666250
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

31666478
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./geno

31666505
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

31666507
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths22.out" > ./genome_analysis/jobscript22.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript22.job 

31666508
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes23.txt /data/timonaj/cancer_as_wound/ppi_analysis/rege

31666537
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths42.out" > ./genome_analysis/jobscript42.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript42.job 

31666538
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes43.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths43.out" > ./genome_analysis/jobscript43.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript43.job 

31666539
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes44.txt /data/timonaj/cancer_as_wound/ppi_analysis/rege

31666566
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes63.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths63.out" > ./genome_analysis/jobscript63.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript63.job 

31666567
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes64.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths64.out" > ./genome_analysis/jobscript64.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript64.job 

31666568
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes65.txt /data/timonaj/cancer_as_wound/ppi_analysis/rege

31666600
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes84.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths84.out" > ./genome_analysis/jobscript84.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript84.job 

31666601
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes85.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths85.out" > ./genome_analysis/jobscript85.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript85.job 

31666602
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes86.txt /data/timonaj/cancer_as_wound/ppi_analysis/rege

...

31682456
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1617.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1617.out" > ./genome_analysis/jobscript1617.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1617.job 

31682458
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1618.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1618.out" > ./genome_analysis/jobscript1618.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1618.job 

31682461
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1619.txt /data/timonaj/cancer_as_wound

31682503
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1638.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1638.out" > ./genome_analysis/jobscript1638.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1638.job 

31682505
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1639.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1639.out" > ./genome_analysis/jobscript1639.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1639.job 

31682508
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1640.txt /data/timonaj/cancer_as_wound

31682545
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1659.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1659.out" > ./genome_analysis/jobscript1659.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1659.job 

31682547
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1660.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1660.out" > ./genome_analysis/jobscript1660.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1660.job 

31682548
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1661.txt /data/timonaj/cancer_as_wound

31682584
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1680.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1680.out" > ./genome_analysis/jobscript1680.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1680.job 

31682585
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1681.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1681.out" > ./genome_analysis/jobscript1681.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1681.job 

31682595
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1682.txt /data/timonaj/cancer_as_wound

31682841
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1701.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1701.out" > ./genome_analysis/jobscript1701.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1701.job 

31682843
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1702.txt /data/timonaj/cancer_as_wound/ppi_analysis/regen_genes.txt ./genome_analysis/genome_wrs_paths1702.out" > ./genome_analysis/jobscript1702.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1702.job 

31682845
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1703.txt /data/timonaj/cancer_as_wound

In [ ]:
#wound
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "wound_genes.txt", "genome_wound_paths")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes601.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths601.out" > ./genome_analysis/jobscript601.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript601.job 

31747232
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes602.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths602.out" > ./genome_analysis/jobscript602.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript602.job 

31747233
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes603.txt /data/timonaj/cancer_as_wound/ppi_analysis/

31747256
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes622.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths622.out" > ./genome_analysis/jobscript622.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript622.job 

31747257
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes623.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths623.out" > ./genome_analysis/jobscript623.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript623.job 

31747258
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes624.txt /data/timonaj/cancer_as_wound/ppi_

31747277
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes643.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths643.out" > ./genome_analysis/jobscript643.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript643.job 

31747278
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes644.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths644.out" > ./genome_analysis/jobscript644.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript644.job 

31747279
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes645.txt /data/timonaj/cancer_as_wound/ppi_

31747298
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes664.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths664.out" > ./genome_analysis/jobscript664.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript664.job 

31747299
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes665.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths665.out" > ./genome_analysis/jobscript665.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript665.job 

31747300
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes666.txt /data/timonaj/cancer_as_wound/ppi_

31747321
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes685.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths685.out" > ./genome_analysis/jobscript685.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript685.job 

31747322
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes686.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths686.out" > ./genome_analysis/jobscript686.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript686.job 

31747323
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes687.txt /data/timonaj/cancer_as_wound/ppi_

...

31753755
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1609.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1609.out" > ./genome_analysis/jobscript1609.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1609.job 

31753757
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1610.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1610.out" > ./genome_analysis/jobscript1610.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1610.job 

31753759
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1611.txt /data/timonaj/cancer_as_w

31753780
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1630.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1630.out" > ./genome_analysis/jobscript1630.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1630.job 

31753781
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1631.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1631.out" > ./genome_analysis/jobscript1631.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1631.job 

31753782
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1632.txt /data/timonaj/cancer_as_w

31753804
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1651.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1651.out" > ./genome_analysis/jobscript1651.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1651.job 

31753805
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1652.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1652.out" > ./genome_analysis/jobscript1652.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1652.job 

31753806
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1653.txt /data/timonaj/cancer_as_w

31753828
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1672.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1672.out" > ./genome_analysis/jobscript1672.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1672.job 

31753829
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1673.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1673.out" > ./genome_analysis/jobscript1673.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1673.job 

31753830
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1674.txt /data/timonaj/cancer_as_w

31753853
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1693.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1693.out" > ./genome_analysis/jobscript1693.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1693.job 

31753854
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1694.txt /data/timonaj/cancer_as_wound/ppi_analysis/wound_genes.txt ./genome_analysis/genome_wound_paths1694.out" > ./genome_analysis/jobscript1694.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1694.job 

31753856
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1695.txt /data/timonaj/cancer_as_w

In [ ]:
#wound
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "stress_genes.txt", "genome_stress_paths")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

31769059
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

31769061
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.t

31769101
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

31769103
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths22.out" > ./genome_analysis/jobscript22.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript22.job 

31769105
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes23.txt /data/timonaj/cancer_as_wound/ppi_analy

31769130
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths42.out" > ./genome_analysis/jobscript42.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript42.job 

31769132
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes43.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths43.out" > ./genome_analysis/jobscript43.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript43.job 

31769133
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes44.txt /data/timonaj/cancer_as_wound/ppi_analy

31769155
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes63.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths63.out" > ./genome_analysis/jobscript63.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript63.job 

31769157
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes64.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths64.out" > ./genome_analysis/jobscript64.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript64.job 

31769159
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes65.txt /data/timonaj/cancer_as_wound/ppi_analy

31769180
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes84.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths84.out" > ./genome_analysis/jobscript84.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript84.job 

31769181
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes85.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths85.out" > ./genome_analysis/jobscript85.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript85.job 

31769182
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes86.txt /data/timonaj/cancer_as_wound/ppi_analy

...

31784325
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1108.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1108.out" > ./genome_analysis/jobscript1108.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1108.job 

31784328
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1109.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1109.out" > ./genome_analysis/jobscript1109.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1109.job 

31784331
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1110.txt /data/timonaj/cancer_

31784363
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1128.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1128.out" > ./genome_analysis/jobscript1128.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1128.job 

31784366
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1129.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1129.out" > ./genome_analysis/jobscript1129.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1129.job 

31784371
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1130.txt /data/timonaj/cancer_

31784430
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1148.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1148.out" > ./genome_analysis/jobscript1148.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1148.job 

31784432
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1149.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1149.out" > ./genome_analysis/jobscript1149.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1149.job 

31784434
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1150.txt /data/timonaj/cancer_

31784466
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1168.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1168.out" > ./genome_analysis/jobscript1168.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1168.job 

31784468
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1169.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1169.out" > ./genome_analysis/jobscript1169.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1169.job 

31784469
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1170.txt /data/timonaj/cancer_

31784501
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1188.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1188.out" > ./genome_analysis/jobscript1188.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1188.job 

31784502
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1189.txt /data/timonaj/cancer_as_wound/ppi_analysis/stress_genes.txt ./genome_analysis/genome_stress_paths1189.out" > ./genome_analysis/jobscript1189.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1189.job 

31784504
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1190.txt /data/timonaj/cancer_

In [12]:
for file in os.listdir("/data/timonaj/cancer_as_wound/spec_exp_genes"):
    #genome_genes = [node for node in hPPIN.nodes()]
    print(file)
    print(output)
    output = "genome_" +  file[:-4]
    genome_genes = [node for node in hPPIN.nodes()]
    genome_wrs_distance(genome_genes, "genome_genes", file, output)

sscrofa_wound_down.txt
genome_sscrofa_wound_down
mmusculus_stress_down.txt
genome_mmusculus_stress_down
hsapiens_regen_up.txt
genome_hsapiens_regen_up
celegans_stress_up.txt
genome_celegans_stress_up
amexicanum_regen_down.txt
genome_amexicanum_regen_down
dmelanogaster_wound_down.txt
genome_dmelanogaster_wound_down
rnorvegicus_wound_down.txt
genome_rnorvegicus_wound_down
drerio_regen_down.txt
genome_drerio_regen_down
mmusculus_stress_up.txt
genome_mmusculus_stress_up
hsapiens_regen_down.txt
genome_hsapiens_regen_down
hsapiens_wound_up.txt
genome_hsapiens_wound_up
clupisFamiliaris_wound_down.txt
genome_clupisFamiliaris_wound_down
clupisFamiliaris_wound_up.txt
genome_clupisFamiliaris_wound_up
rnorvegicus_wound_up.txt
genome_rnorvegicus_wound_up
hsapiens_wound_down.txt
genome_hsapiens_wound_down
dmelanogaster_stress_down.txt
genome_dmelanogaster_stress_down
celegans_stress_down.txt
genome_celegans_stress_down
sscrofa_wound_up.txt
genome_sscrofa_wound_up
drerio_regen_up.txt
genome_drerio_re

In [8]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "hsapiens_wound_up.txt", "genome_hsapiens_wound_up")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

32849459
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

32849460
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj/cancer_as_wound/ppi_ana

32849487
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

32849488
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up22.out" > ./genome_analysis/jobscript22.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript22.job 

32849489
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes23.txt /data/timonaj/cance

32849507
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

32849508
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up42.out" > ./genome_analysis/jobscript42.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript42.job 

32849509
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes43.txt /data/timonaj/cance

32849541
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes61.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up61.out" > ./genome_analysis/jobscript61.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript61.job 

32849543
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes62.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up62.out" > ./genome_analysis/jobscript62.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript62.job 

32849545
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes63.txt /data/timonaj/cance

32849581
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes81.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up81.out" > ./genome_analysis/jobscript81.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript81.job 

32849583
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes82.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up82.out" > ./genome_analysis/jobscript82.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript82.job 

32849585
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes83.txt /data/timonaj/cance

...

32855097
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1621.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1621.out" > ./genome_analysis/jobscript1621.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1621.job 

32855098
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1622.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1622.out" > ./genome_analysis/jobscript1622.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1622.job 

32855100
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1623.txt /

32855126
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1641.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1641.out" > ./genome_analysis/jobscript1641.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1641.job 

32855127
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1642.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1642.out" > ./genome_analysis/jobscript1642.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1642.job 

32855128
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1643.txt /

32855152
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1661.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1661.out" > ./genome_analysis/jobscript1661.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1661.job 

32855153
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1662.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1662.out" > ./genome_analysis/jobscript1662.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1662.job 

32855154
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1663.txt /

32855182
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1681.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1681.out" > ./genome_analysis/jobscript1681.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1681.job 

32855184
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1682.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1682.out" > ./genome_analysis/jobscript1682.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1682.job 

32855185
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1683.txt /

32855205
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1701.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1701.out" > ./genome_analysis/jobscript1701.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1701.job 

32855206
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1702.txt /data/timonaj/cancer_as_wound/ppi_analysis/hsapiens_wound_up.txt ./genome_analysis/genome_hsapiens_wound_up1702.out" > ./genome_analysis/jobscript1702.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1702.job 

32855207
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1703.txt /

In [9]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "amexicanum_regen_up.txt", "genome_amexicanum_regen_up")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

32855212
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

32855213
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj/cancer_as_wound

32855241
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes20.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up20.out" > ./genome_analysis/jobscript20.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript20.job 

32855242
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

32855243
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22.txt /data/timon

32855266
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes40.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up40.out" > ./genome_analysis/jobscript40.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript40.job 

32855267
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

32855268
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42.txt /data/timon

32855292
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes60.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up60.out" > ./genome_analysis/jobscript60.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript60.job 

32855293
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes61.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up61.out" > ./genome_analysis/jobscript61.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript61.job 

32855294
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes62.txt /data/timon

32855314
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes80.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up80.out" > ./genome_analysis/jobscript80.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript80.job 

32855315
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes81.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up81.out" > ./genome_analysis/jobscript81.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript81.job 

32855316
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes82.txt /data/timon

...

32859481
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1620.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1620.out" > ./genome_analysis/jobscript1620.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1620.job 

32859484
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1621.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1621.out" > ./genome_analysis/jobscript1621.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1621.job 

32859486
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

32859525
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1640.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1640.out" > ./genome_analysis/jobscript1640.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1640.job 

32859527
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1641.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1641.out" > ./genome_analysis/jobscript1641.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1641.job 

32859529
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

32859567
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1660.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1660.out" > ./genome_analysis/jobscript1660.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1660.job 

32859569
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1661.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1661.out" > ./genome_analysis/jobscript1661.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1661.job 

32859571
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

32859610
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1680.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1680.out" > ./genome_analysis/jobscript1680.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1680.job 

32859612
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1681.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1681.out" > ./genome_analysis/jobscript1681.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1681.job 

32859613
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

32859631
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1700.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1700.out" > ./genome_analysis/jobscript1700.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1700.job 

32859634
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1701.txt /data/timonaj/cancer_as_wound/ppi_analysis/amexicanum_regen_up.txt ./genome_analysis/genome_amexicanum_regen_up1701.out" > ./genome_analysis/jobscript1701.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1701.job 

32859636
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes17

In [ ]:
#sscrofa_wound_up
#rnorvegicus_wound_up
mmusculus_stress_up
#hsapiens_wound_up
#hsapiens_wound_down
#hsapiens_stress_down
#hsapiens_regen_down
#drerio_regen_up
dmelanogaster_stress_up
dmelanogaster_stress_down
#clupisFamiliaris_wound_up
#clupisFamiliaris_wound_down
celegans_stress_down

In [7]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "clupisFamiliaris_wound_down.txt", "clupisFamiliaris_wound_down")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

33123387
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

33123389
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timon

33123408
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes20.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down20.out" > ./genome_analysis/jobscript20.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript20.job 

33123409
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

33123410
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes

33123609
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes40.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down40.out" > ./genome_analysis/jobscript40.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript40.job 

33123690
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

33123691
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes

33123711
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes60.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down60.out" > ./genome_analysis/jobscript60.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript60.job 

33123712
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes61.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down61.out" > ./genome_analysis/jobscript61.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript61.job 

33123713
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes

33123737
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes80.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down80.out" > ./genome_analysis/jobscript80.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript80.job 

33123738
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes81.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down81.out" > ./genome_analysis/jobscript81.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript81.job 

33123740
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes

...

33132263
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1627.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1627.out" > ./genome_analysis/jobscript1627.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1627.job 

33132264
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1628.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1628.out" > ./genome_analysis/jobscript1628.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1628.job 

33132265
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analy

33132282
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1646.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1646.out" > ./genome_analysis/jobscript1646.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1646.job 

33132283
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1647.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1647.out" > ./genome_analysis/jobscript1647.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1647.job 

33132285
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analy

33132307
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1665.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1665.out" > ./genome_analysis/jobscript1665.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1665.job 

33132308
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1666.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1666.out" > ./genome_analysis/jobscript1666.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1666.job 

33132309
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analy

33132351
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1684.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1684.out" > ./genome_analysis/jobscript1684.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1684.job 

33132352
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1685.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1685.out" > ./genome_analysis/jobscript1685.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1685.job 

33132353
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analy

33132371
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1703.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1703.out" > ./genome_analysis/jobscript1703.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1703.job 

33132372
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1704.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_down.txt ./genome_analysis/clupisFamiliaris_wound_down1704.out" > ./genome_analysis/jobscript1704.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1704.job 

33132373
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analy

In [8]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "clupisFamiliaris_wound_up.txt", "genome_clupisFamiliaris_wound_up")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

33132376
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

33132377
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data

33132399
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes20.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up20.out" > ./genome_analysis/jobscript20.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript20.job 

33132400
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

33132401
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome

33132420
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes40.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up40.out" > ./genome_analysis/jobscript40.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript40.job 

33132421
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

33132422
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome

33132442
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes60.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up60.out" > ./genome_analysis/jobscript60.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript60.job 

33132443
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes61.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up61.out" > ./genome_analysis/jobscript61.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript61.job 

33132444
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome

33132494
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes80.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up80.out" > ./genome_analysis/jobscript80.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript80.job 

33132495
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes81.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up81.out" > ./genome_analysis/jobscript81.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript81.job 

33132496
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome

...

33140814
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1620.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1620.out" > ./genome_analysis/jobscript1620.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1620.job 

33140815
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1621.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1621.out" > ./genome_analysis/jobscript1621.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1621.job 

33140818
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome

33140902
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1639.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1639.out" > ./genome_analysis/jobscript1639.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1639.job 

33140904
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1640.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1640.out" > ./genome_analysis/jobscript1640.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1640.job 

33140905
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome

33140926
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1658.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1658.out" > ./genome_analysis/jobscript1658.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1658.job 

33140927
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1659.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1659.out" > ./genome_analysis/jobscript1659.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1659.job 

33140928
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome

33140945
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1677.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1677.out" > ./genome_analysis/jobscript1677.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1677.job 

33140946
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1678.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1678.out" > ./genome_analysis/jobscript1678.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1678.job 

33140947
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome

33140967
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1696.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1696.out" > ./genome_analysis/jobscript1696.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1696.job 

33140968
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1697.txt /data/timonaj/cancer_as_wound/ppi_analysis/clupisFamiliaris_wound_up.txt ./genome_analysis/genome_clupisFamiliaris_wound_up1697.out" > ./genome_analysis/jobscript1697.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1697.job 

33140969
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome

In [9]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "celegans_stress_down.txt", "genome_celegans_stress_down")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

33140987
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

33140988
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj/cancer_as_w

33141043
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes20.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down20.out" > ./genome_analysis/jobscript20.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript20.job 

33141044
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

33141048
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22.txt /data/t

33141099
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes40.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down40.out" > ./genome_analysis/jobscript40.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript40.job 

33141101
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

33141103
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42.txt /data/t

33141129
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes60.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down60.out" > ./genome_analysis/jobscript60.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript60.job 

33141130
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes61.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down61.out" > ./genome_analysis/jobscript61.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript61.job 

33141131
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes62.txt /data/t

33141152
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes80.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down80.out" > ./genome_analysis/jobscript80.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript80.job 

33141153
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes81.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down81.out" > ./genome_analysis/jobscript81.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript81.job 

33141154
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes82.txt /data/t

...

33146769
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1620.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1620.out" > ./genome_analysis/jobscript1620.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1620.job 

33146770
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1621.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1621.out" > ./genome_analysis/jobscript1621.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1621.job 

33146771
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_gen

33146797
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1640.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1640.out" > ./genome_analysis/jobscript1640.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1640.job 

33146799
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1641.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1641.out" > ./genome_analysis/jobscript1641.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1641.job 

33146800
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_gen

33146823
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1660.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1660.out" > ./genome_analysis/jobscript1660.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1660.job 

33146824
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1661.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1661.out" > ./genome_analysis/jobscript1661.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1661.job 

33146825
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_gen

33147235
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1680.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1680.out" > ./genome_analysis/jobscript1680.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1680.job 

33147237
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1681.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1681.out" > ./genome_analysis/jobscript1681.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1681.job 

33147241
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_gen

33147312
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1700.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1700.out" > ./genome_analysis/jobscript1700.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1700.job 

33147315
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1701.txt /data/timonaj/cancer_as_wound/ppi_analysis/celegans_stress_down.txt ./genome_analysis/genome_celegans_stress_down1701.out" > ./genome_analysis/jobscript1701.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1701.job 

33147318
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_gen

In [10]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "mmusculus_stress_up.txt", "genome_mmusculus_stress_up")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

33147337
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

33147340
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj/cancer_as_wound

33147399
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes20.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up20.out" > ./genome_analysis/jobscript20.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript20.job 

33147403
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

33147407
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22.txt /data/timon

33147472
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes40.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up40.out" > ./genome_analysis/jobscript40.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript40.job 

33147474
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

33147477
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42.txt /data/timon

33147534
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes60.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up60.out" > ./genome_analysis/jobscript60.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript60.job 

33147540
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes61.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up61.out" > ./genome_analysis/jobscript61.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript61.job 

33147543
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes62.txt /data/timon

33147628
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes80.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up80.out" > ./genome_analysis/jobscript80.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript80.job 

33147630
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes81.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up81.out" > ./genome_analysis/jobscript81.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript81.job 

33147633
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes82.txt /data/timon

...

33153453
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1620.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1620.out" > ./genome_analysis/jobscript1620.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1620.job 

33153454
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1621.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1621.out" > ./genome_analysis/jobscript1621.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1621.job 

33153462
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

33153482
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1640.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1640.out" > ./genome_analysis/jobscript1640.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1640.job 

33153483
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1641.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1641.out" > ./genome_analysis/jobscript1641.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1641.job 

33153484
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

33153511
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1660.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1660.out" > ./genome_analysis/jobscript1660.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1660.job 

33153512
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1661.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1661.out" > ./genome_analysis/jobscript1661.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1661.job 

33153514
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

33153541
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1680.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1680.out" > ./genome_analysis/jobscript1680.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1680.job 

33153542
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1681.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1681.out" > ./genome_analysis/jobscript1681.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1681.job 

33153546
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes16

33153582
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1700.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1700.out" > ./genome_analysis/jobscript1700.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1700.job 

33153583
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1701.txt /data/timonaj/cancer_as_wound/ppi_analysis/mmusculus_stress_up.txt ./genome_analysis/genome_mmusculus_stress_up1701.out" > ./genome_analysis/jobscript1701.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1701.job 

33153584
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes17

In [ ]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "dmelanogaster_stress_up.txt", "genome_dmelanogaster_stress_up")

printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes0.txt /data/timonaj/cancer_as_wound/ppi_analysis/dmelanogaster_stress_up.txt ./genome_analysis/genome_dmelanogaster_stress_up0.out" > ./genome_analysis/jobscript0.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript0.job 

33153591
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes1.txt /data/timonaj/cancer_as_wound/ppi_analysis/dmelanogaster_stress_up.txt ./genome_analysis/genome_dmelanogaster_stress_up1.out" > ./genome_analysis/jobscript1.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript1.job 

33153592
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes2.txt /data/timonaj

33153614
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes20.txt /data/timonaj/cancer_as_wound/ppi_analysis/dmelanogaster_stress_up.txt ./genome_analysis/genome_dmelanogaster_stress_up20.out" > ./genome_analysis/jobscript20.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript20.job 

33153615
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes21.txt /data/timonaj/cancer_as_wound/ppi_analysis/dmelanogaster_stress_up.txt ./genome_analysis/genome_dmelanogaster_stress_up21.out" > ./genome_analysis/jobscript21.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript21.job 

33153616
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes22

33153636
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes40.txt /data/timonaj/cancer_as_wound/ppi_analysis/dmelanogaster_stress_up.txt ./genome_analysis/genome_dmelanogaster_stress_up40.out" > ./genome_analysis/jobscript40.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript40.job 

33153637
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes41.txt /data/timonaj/cancer_as_wound/ppi_analysis/dmelanogaster_stress_up.txt ./genome_analysis/genome_dmelanogaster_stress_up41.out" > ./genome_analysis/jobscript41.job 
sbatch --mem=1g --cpus-per-task=2 --gres=lscratch:2 --time 4:00:00 ./genome_analysis/jobscript41.job 

33153640
printf "#!/bin/bash
module load python
python /data/timonaj/cancer_as_wound/ppi_analysis/wrs_shortest_paths.py ./genome_analysis/genome_genes42

In [ ]:
genome_genes = [node for node in hPPIN.nodes()]
genome_wrs_distance(genome_genes, "genome_genes", "dmelanogaster_stress_down.txt", "genome_dmelanogaster_stress_down")